# <font color="#880000"> Using the nexsciTAP Server with the TAP+ Client to Access LWS or NIRC Data From KOA In Synchronous Mode

## <font color="#880000"> The nexsciTAP server
The NASA Exoplanet Science Institute (NExScI) (visit https://nexsci.caltech.edu) has developed a Python-based server to implement an API that complies with the Virtual Observatory (VO) Table Access Protocol(TAP) version 1.1 (September 2019) (http://ivoa.net/documents/TAP/20190927/index.html), a standard recommended by the International Virtual Observatory alliance (IVOA) (http://ivoa.net). 

The TAP API enables a rich variety of searches against tabular data, includung cone, box or all-sky searches, temporal searches, combinations of spatial searches and temporal searches, searches against instrumental attributes and program attributes. 

This tutorial supports demonstrates how to use the TAP+ client to perform synchronous TAP-based queries for public raw science and calibration data acquired with the the Long Wavelength Spectrometer (LWS) or  Near Infrared Camera (NIRC); these data are hosted at the Keck Observatory Archive  (KOA; https://koa.ipac.caltech.edu).
 
#### <font color="#880000"> Requirements </font> 
TAP+ was developed at the ESAC Space Data Centre (ESDC: http://www.cosmos.esa.int/web/esdc/) and can be installed from PyPI as part of the astroquery package:

$ pip  install   --upgrade   astroquery

The tutorial requires Python 3.6 (or above), plus the table read and write functions from Astropy.  We have tested with Astropy 4.0.1, but any version should work.  We recommend using the Ananconda Python distribution.

#### <font color="#880000"> A note on output records </font> 
#### The number of records returned here may differ from those returned here because new data are released daily.  In synchronous mode, the TAP+ client returns the first 2,000 records returned.

#### Version 1.0 (August, 2021)


### Set up

In [1]:
print("import os")
print("import numpy as np")
print("from astroquery.utils.tap.core import TapPlus")
print("koa = TapPlus(url=\"https://koa.ipac.caltech.edu/TAP\")")
print(" ")
print('─' * 10)
print(" ")

import os
import numpy as np
from astroquery.utils.tap.core import TapPlus
koa = TapPlus(url="https://koa.ipac.caltech.edu/TAP")


import os
import numpy as np
from astroquery.utils.tap.core import TapPlus
koa = TapPlus(url="https://koa.ipac.caltech.edu/TAP")
 
──────────
 
Created TAP+ (v20200428.1) - Connection:
	Host: koa.ipac.caltech.edu
	Use HTTPS: True
	Port: 443
	SSL Port: 443


## Define instrument
Uncomment the instrument below for either LWS or NIRC

In [2]:
# Uncomment below for LWS
instrument = 'LWS'

# Uncomment for NIRC
#instrument = 'NIRC'



## Define search parameters

In [3]:
if (instrument == 'LWS'):
    instr = 'lws'
    koatable = 'koa_lws'    
    outdir = './outputLW_tapplus_sync/'
    koaid_date = '19981203'
    startdate = '1998-12-03 00:00:00'
    enddate = '1998-12-27 23:59:59'
    date = '1998-12-03'
    program = 'A078LS'
    circle_pos = '68.98 16.51 1.0'
    box_pos = '68.98 16.51 0.5 0.5'
    polygon_pos = '67.98,15.51,67.98,17.51,70.98,22.03'

if (instrument == 'NIRC'):
    instr = 'nirc'
    koatable = 'koa_nirc'
    outdir = './outputN1_tapplus_sync/'
    koaid_date = '19950316'
    startdate = '1995-03-16 00:00:00'
    enddate = '1995-04-01 23:59:59'
    date = '1995-03-16'
    program = 'U41N'
    circle_pos = '162.07 12.63 1.0'
    box_pos = '162.07 12.63 0.5 0.5'
    polygon_pos = '161.07,11.63,161.07,13.63,164.07,12.63'


## Create output directory

In [4]:
print("try:")
print("\tos.mkdir('" + outdir + "')")
print("except:")
print("\tprint (\" " + instrument + " Directory exists already\", flush=True)")
print(" ")
print('─' * 10)
print(" ")

try:
    os.mkdir(outdir)
except:
    print(instrument + " Directory exists already", flush=True)

try:
	os.mkdir('./outputLW_tapplus_sync/')
except:
	print (" LWS Directory exists already", flush=True)
 
──────────
 


### Search by date

In [5]:
print("sql = \"select koaid, filehand from " + koatable + " where koaid like '%" + koaid_date + "%' \"")
print("job = koa.launch_job(sql)")
print("r = job.get_results()")
print("print(r)")
print(" ")
print('─' * 10)
print(" ")

sql = "select koaid, filehand from " + koatable + " where koaid like '%" + koaid_date + "%'"
job = koa.launch_job(sql)
r = job.get_results()
print(r)

sql = "select koaid, filehand from koa_lws where koaid like '%19981203%' "
job = koa.launch_job(sql)
r = job.get_results()
print(r)
 
──────────
 
        koaid                                filehand                     
---------------------- ---------------------------------------------------
LW.19981203.08419.fits /koadata31/LWS/19981203/lev0/LW.19981203.08419.fits
LW.19981203.55485.fits /koadata31/LWS/19981203/lev0/LW.19981203.55485.fits
LW.19981203.59695.fits /koadata31/LWS/19981203/lev0/LW.19981203.59695.fits
LW.19981203.55023.fits /koadata31/LWS/19981203/lev0/LW.19981203.55023.fits
LW.19981203.57381.fits /koadata31/LWS/19981203/lev0/LW.19981203.57381.fits
LW.19981203.55703.fits /koadata31/LWS/19981203/lev0/LW.19981203.55703.fits
LW.19981203.56388.fits /koadata31/LWS/19981203/lev0/LW.19981203.56388.fits
LW.19981203.56623.fits /koadata31/LWS/19981203/lev0/LW.19981203.56623.fits
LW.19981203.56888.fits /koadata31/LWS/19981203/lev0/LW.19981203.56888.fits
LW.19981203.57719.fits /koad

###  Write the output to the IPAC ASCII, VOtable CSV and TSV formats

In [6]:
print("job = koa.launch_job(sql, dump_to_file=True, output_file= " + outdir + instr + "_KoaTapDate1.tbl, output_format='ipac')")
print("job = koa.launch_job(sql, dump_to_file=True, output_file= " + outdir + instr + "_KoaTapDate2.vot, output_format='votable')")
print("job = koa.launch_job(sql, dump_to_file=True, output_file= " + outdir + instr + "_KoaTapDate3.csv, output_format='csv')")
print("job = koa.launch_job(sql, dump_to_file=True, output_file= " + outdir + instr + "_KoaTapDate4.tsv, output_format='tsv')")
print(" ")
print('─' * 10)
print(" ")

job = koa.launch_job(sql, dump_to_file=True, output_file= outdir + instr + "_KoaTapDate1.tbl", output_format='ipac')
job = koa.launch_job(sql, dump_to_file=True, output_file= outdir + instr + "_KoaTapDate2.vot", output_format='votable')
job = koa.launch_job(sql, dump_to_file=True, output_file= outdir + instr + "_KoaTapDate3.csv", output_format='csv')
job = koa.launch_job(sql, dump_to_file=True, output_file= outdir + instr + "_KoaTapDate4.tsv", output_format='tsv')

job = koa.launch_job(sql, dump_to_file=True, output_file= ./outputLW_tapplus_sync/lws_KoaTapDate1.tbl, output_format='ipac')
job = koa.launch_job(sql, dump_to_file=True, output_file= ./outputLW_tapplus_sync/lws_KoaTapDate2.vot, output_format='votable')
job = koa.launch_job(sql, dump_to_file=True, output_file= ./outputLW_tapplus_sync/lws_KoaTapDate3.csv, output_format='csv')
job = koa.launch_job(sql, dump_to_file=True, output_file= ./outputLW_tapplus_sync/lws_KoaTapDate4.tsv, output_format='tsv')
 
──────────
 


## Select all keywords for data acquired on UT date 

In [7]:
print("sql = \"select * from " + koatable + " where koaid like '%" + koaid_date + "%'\"")
print("job = koa.launch_job(sql)")
print("r = job.get_results()")
print("print(r)")
print("job = koa.launch_job(sql, dump_to_file=True, output_file='" + outdir  + instr + "_table_ascii.tbl', output_format='ipac')")
print(" ")
print('─' * 10)
print(" ")

sql = "select * from " + koatable + " where koaid like '%" + koaid_date + "%'"
job = koa.launch_job(sql)
r = job.get_results()
print(r)

job = koa.launch_job(sql, dump_to_file=True, output_file=outdir + instr + "_table_ascii.tbl", \
                     output_format='ipac')

sql = "select * from koa_lws where koaid like '%19981203%'"
job = koa.launch_job(sql)
r = job.get_results()
print(r)
job = koa.launch_job(sql, dump_to_file=True, output_file='./outputLW_tapplus_sync/lws_table_ascii.tbl', output_format='ipac')
 
──────────
 
        koaid              ofname     propint ...         z           spt_ind 
---------------------- -------------- ------- ... ------------------ ---------
LW.19981203.08419.fits   lws0001.fits      18 ...   0.94128377839366 231320231
LW.19981203.55485.fits   irc0080.fits      18 ...   0.22971800335177 220221323
LW.19981203.59695.fits   irc0102.fits      18 ...  0.229531147144593 220221323
LW.19981203.55023.fits   irc0078.fits      18 ...   0.22971800335177 220221323
LW.19981203.57381.fits   irc0090.fits      18 ...  0.229701016773622 220221323
LW.19981203.55703.fits   irc0082.fits      18 ...   0.22971800335177 220221323
LW.19981203.56388.fits   irc0084.fits      18 ...  0.229701016773622 220221323
LW.19981203.56623.fits   irc008

###  Select columns acquired on UT Date 

In [8]:
print("sql = \"select koaid, filehand from " + koatable + " where koaid like '%" + koaid_date + "%'\"")
print("job = koa.launch_job(sql)")
print("r = job.get_results()")
print("print(r)")
print("job = koa.launch_job(sql, dump_to_file=True, output_file='" + outdir + instr + "_columns.tbl', output_format='ipac')")
print(" ")
print('─' * 10)
print(" ")


sql = "select koaid, filehand from " + koatable + " where koaid like '%" + koaid_date + "%'"
job = koa.launch_job(sql)
r = job.get_results()
print(r)
job = koa.launch_job(sql, dump_to_file=True, output_file= outdir + instr + "_columns.tbl", output_format='ipac')

sql = "select koaid, filehand from koa_lws where koaid like '%19981203%'"
job = koa.launch_job(sql)
r = job.get_results()
print(r)
job = koa.launch_job(sql, dump_to_file=True, output_file='./outputLW_tapplus_sync/lws_columns.tbl', output_format='ipac')
 
──────────
 
        koaid                                filehand                     
---------------------- ---------------------------------------------------
LW.19981203.08419.fits /koadata31/LWS/19981203/lev0/LW.19981203.08419.fits
LW.19981203.55485.fits /koadata31/LWS/19981203/lev0/LW.19981203.55485.fits
LW.19981203.59695.fits /koadata31/LWS/19981203/lev0/LW.19981203.59695.fits
LW.19981203.55023.fits /koadata31/LWS/19981203/lev0/LW.19981203.55023.fits
LW.19981203.57381.fits /koadata31/LWS/19981203/lev0/LW.19981203.57381.fits
LW.19981203.55703.fits /koadata31/LWS/19981203/lev0/LW.19981203.55703.fits
LW.19981203.56388.fits /koadata31/LWS/19981203/lev0/LW.19981203.56388.fits
LW.19981203.56623.fits /koadata31/LWS/19981203/lev0/LW.19

## Select a maximum number of records 

In [9]:
print("sql = \"select top 20 koaid, filehand, frameno from " + koatable + " where koaid like '%" + koaid_date + "%'\"")
print("job = koa.launch_job(sql, dump_to_file=True, output_file='" + outdir + instr + "_KoaTapTestFiniteRecors.tbl', output_format='ipac')")
print("job = koa.launch_job(sql)")
print("r = job.get_results()")
print("print(r)")
print("job = koa.launch_job(sql, dump_to_file=True, output_file='" + outdir + instr + "_top20.tbl', output_format='ipac')")
print(" ")
print('─' * 10)
print(" ")


sql = "select top 20 koaid, filehand, frameno from " + koatable + " where koaid like '%" + koaid_date + "%'"
job = koa.launch_job(sql, dump_to_file=True, output_file=  outdir + instr + "_KoaTapTestFiniteRecors.tbl", output_format='ipac')
job = koa.launch_job(sql)
r = job.get_results()
print(r)
job = koa.launch_job(sql, dump_to_file=True, output_file=  outdir + instr + "_top20.tbl", output_format='ipac')

sql = "select top 20 koaid, filehand, frameno from koa_lws where koaid like '%19981203%'"
job = koa.launch_job(sql, dump_to_file=True, output_file='./outputLW_tapplus_sync/lws_KoaTapTestFiniteRecors.tbl', output_format='ipac')
job = koa.launch_job(sql)
r = job.get_results()
print(r)
job = koa.launch_job(sql, dump_to_file=True, output_file='./outputLW_tapplus_sync/lws_top20.tbl', output_format='ipac')
 
──────────
 
        koaid          ... frameno
---------------------- ... -------
LW.19981203.08419.fits ...       1
LW.19981203.55485.fits ...      80
LW.19981203.59695.fits ...     102
LW.19981203.55023.fits ...      78
LW.19981203.57381.fits ...      90
LW.19981203.55703.fits ...      82
LW.19981203.56388.fits ...      84
LW.19981203.56623.fits ...      86
LW.19981203.56888.fits ...      88
LW.19981203.57719.fits ...      92
LW.19981203.59336.fits ...      98
LW.19981203.58397.fits ...      94
LW.19981203.58630.fits ...      95
LW.19981203.59572.fits ...     101
LW.19981203.59487.fit

## Select columns and search by datetime range

In [10]:
print("sql = \"select koaid, filehand from " + koatable + " where (utdatetime >= to_date('" + startdate +"', 'yyyy-mm-dd HH24:MI:SS') and utdatetime <= to_date('" + enddate + "', 'yyyy-mm-dd HH24:MI:SS'))\"")
print("job = koa.launch_job(sql)");
print("r = job.get_results()");
print("print(r)")
print("job = koa.launch_job(sql, dump_to_file=True, output_file='" + outdir + instr + "_datetime_range.tbl', output_format='ipac')")
print(" ")
print('─' * 10)
print(" ")

sql = "select koaid, filehand from " + koatable + " where (utdatetime >= to_date('" + startdate + "', 'yyyy-mm-dd HH24:MI:SS') and utdatetime <= to_date('" + enddate + "', 'yyyy-mm-dd HH24:MI:SS'))"
job = koa.launch_job(sql)
r = job.get_results()
print(r)
job = koa.launch_job(sql, dump_to_file=True, output_file= outdir + instr + "_datetime_range.tbl", output_format='ipac')

sql = "select koaid, filehand from koa_lws where (utdatetime >= to_date('1998-12-03 00:00:00', 'yyyy-mm-dd HH24:MI:SS') and utdatetime <= to_date('1998-12-27 23:59:59', 'yyyy-mm-dd HH24:MI:SS'))"
job = koa.launch_job(sql)
r = job.get_results()
print(r)
job = koa.launch_job(sql, dump_to_file=True, output_file='./outputLW_tapplus_sync/lws_datetime_range.tbl', output_format='ipac')
 
──────────
 
        koaid                                filehand                     
---------------------- ---------------------------------------------------
LW.19981227.32380.fits /koadata31/LWS/19981227/lev0/LW.19981227.32380.fits
LW.19981227.47503.fits /koadata31/LWS/19981227/lev0/LW.19981227.47503.fits
LW.19981227.47636.fits /koadata31/LWS/19981227/lev0/LW.19981227.47636.fits
LW.19981227.47724.fits /koadata31/LWS/19981227/lev0/LW.19981227.47724.fits
LW.19981227.47904.fits /koadata31/LWS/19981227/lev0/LW.19981227.47904.fits
LW.19981227.47993.fits /koadata31/LWS/19981227/lev0/LW.19981227.47993.fits
LW.

## Search by program ID

In [11]:
print("sql= (\"select koaid, filehand, progid from " + koatable + " where (progid = '" + program + "')\")")
print("job = koa.launch_job(sql)")
print("r = job.get_results()")
print("print(r)")
print("job = koa.launch_job(sql, dump_to_file=True, output_file='" + outdir + instr + "_progID.tbl', output_format='ipac')")
print(" ")
print('─' * 10)
print(" ")


sql= ("select koaid, filehand, progid from " + koatable + " where (progid = '" + program  + "')")
job = koa.launch_job(sql)
r = job.get_results()
print(r)
job = koa.launch_job(sql, dump_to_file=True, output_file= outdir + instr + "_progID.tbl", output_format='ipac')

sql= ("select koaid, filehand, progid from koa_lws where (progid = 'A078LS')")
job = koa.launch_job(sql)
r = job.get_results()
print(r)
job = koa.launch_job(sql, dump_to_file=True, output_file='./outputLW_tapplus_sync/lws_progID.tbl', output_format='ipac')
 
──────────
 
        koaid          ... progid
---------------------- ... ------
LW.20050219.22427.fits ... A078LS
LW.20050219.22529.fits ... A078LS
LW.20050219.23025.fits ... A078LS
LW.20050219.23128.fits ... A078LS
LW.20050219.23332.fits ... A078LS
LW.20050219.23433.fits ... A078LS
LW.20050219.23865.fits ... A078LS
LW.20050219.24609.fits ... A078LS
LW.20050219.24710.fits ... A078LS
LW.20050219.24926.fits ... A078LS
                   ... ...    ...
LW.20050220.42462.fits ... A078LS
LW.20050220.43116.fits ... A078LS
LW.20050220.43477.fits ... A078LS
LW.20050220.45889.fits ... A078LS
LW.20050220.49828.fits ... A078LS
LW.20050220.50336.fits ... A078LS
LW.20050220.50700.fits ... A078LS
LW.20050220.51124.fits ... A078LS
LW.20050220.51


##  Spatial cone search 

In [12]:
print("sql=(\"select koaid, filehand,ra, dec from " + koatable + " where contains(point('icrs', ra, dec), circle('icrs', " + circle_pos + ")) = 1\")")
print("job = koa.launch_job(sql)")
print("r = job.get_results()")
print("print(r)")
print("job = koa.launch_job(sql, dump_to_file=True, output_file='" + outdir + instr + "_Spatial_cone.txt', output_format='ipac')")
print(" ")
print('─' * 10)
print(" ")

sql=("select koaid, filehand,ra, dec from " + koatable + " where contains(point('icrs', ra, dec), circle('icrs', " + circle_pos + ")) = 1")
job = koa.launch_job(sql)
r = job.get_results()
print(r)
job = koa.launch_job(sql, dump_to_file=True, output_file= outdir + instr + "_Spatial_cone.txt", output_format='ipac')

sql=("select koaid, filehand,ra, dec from koa_lws where contains(point('icrs', ra, dec), circle('icrs', 68.98 16.51 1.0)) = 1")
job = koa.launch_job(sql)
r = job.get_results()
print(r)
job = koa.launch_job(sql, dump_to_file=True, output_file='./outputLW_tapplus_sync/lws_Spatial_cone.txt', output_format='ipac')
 
──────────
 
        koaid          ...   dec   
---------------------- ... --------
LW.20050219.26119.fits ...   16.508
LW.20050219.26167.fits ...   16.509
LW.20050219.26268.fits ...   16.508
LW.20050219.26436.fits ...   16.508
LW.20050219.26018.fits ...    16.51
LW.20050219.26334.fits ...   16.509
LW.20050220.22673.fits ...    16.51
LW.20050220.29357.fits ...    16.51
LW.20050220.29528.fits ...   16.509
LW.20050220.22843.fits ...   16.508
                   ... ...      ...
LW.19991123.35589.fits ... 16.50949
LW.19990902.50388.fits ...   16.508
LW.19990902.50306.fits ...   16.508
LW.19990902.50775.fits ...   16.509
LW.19990902.54480.fits ...   16.509
LW.19990902.54570.fits ..

##  Spatial box search 

In [13]:
print("sql=(\"select koaid, filehand,ra, dec from " + koatable + " where contains(point('J2000', ra, dec), box('J2000', " + box_pos + ")) = 1\")")
print("job = koa.launch_job(sql)")
print("r = job.get_results()")
print("print(r)")
print("job = koa.launch_job(sql, dump_to_file=True, output_file='" + outdir + instr + "_Spatial_box.txt', output_format='ipac')")
print(" ")
print('─' * 10)
print(" ")

sql=("select koaid, filehand,ra, dec from " + koatable + " where contains(point('J2000', ra, dec), box('J2000', " + box_pos + ")) = 1")
job = koa.launch_job(sql)
r = job.get_results()
print(r)
job = koa.launch_job(sql, dump_to_file=True, output_file= outdir + instr + "_Spatial_box.txt", output_format='ipac')


sql=("select koaid, filehand,ra, dec from koa_lws where contains(point('J2000', ra, dec), box('J2000', 68.98 16.51 0.5 0.5)) = 1")
job = koa.launch_job(sql)
r = job.get_results()
print(r)
job = koa.launch_job(sql, dump_to_file=True, output_file='./outputLW_tapplus_sync/lws_Spatial_box.txt', output_format='ipac')
 
──────────
 
        koaid          ...   dec   
---------------------- ... --------
LW.20050219.26119.fits ...   16.508
LW.20050219.26167.fits ...   16.509
LW.20050219.26268.fits ...   16.508
LW.20050219.26436.fits ...   16.508
LW.20050219.26018.fits ...    16.51
LW.20050219.26334.fits ...   16.509
LW.20050220.22673.fits ...    16.51
LW.20050220.29357.fits ...    16.51
LW.20050220.29528.fits ...   16.509
LW.20050220.22843.fits ...   16.508
                   ... ...      ...
LW.19991123.35589.fits ... 16.50949
LW.19990902.50388.fits ...   16.508
LW.19990902.50306.fits ...   16.508
LW.19990902.50775.fits ...   16.509
LW.19990902.54480.fits ...   16.509
LW.19990902.54570.fits 


## Spatial polygon search 


In [14]:
print("sql=(\"select koaid, filehand,ra, dec from " + koatable + " where contains(point('J2000', ra, dec), polygon('J2000', " + polygon_pos + ")) = 1\")")
print("job = koa.launch_job(sql)")
print("r = job.get_results()")
print("print(r)")
print("job = koa.launch_job(sql, dump_to_file=True, output_file='" + outdir + instr + "_Spatial_polygon.txt', output_format='ipac')")
print(" ")
print('─' * 10)
print(" ")

sql=("select koaid, filehand,ra, dec from " + koatable + " where contains(point('J2000', ra, dec), polygon('J2000', " + polygon_pos + ")) = 1")
job = koa.launch_job(sql)
r = job.get_results()
print(r)
job = koa.launch_job(sql, dump_to_file=True, output_file= outdir + instr + "_Spatial_polygon.txt", output_format='ipac')


sql=("select koaid, filehand,ra, dec from koa_lws where contains(point('J2000', ra, dec), polygon('J2000', 67.98,15.51,67.98,17.51,70.98,22.03)) = 1")
job = koa.launch_job(sql)
r = job.get_results()
print(r)
job = koa.launch_job(sql, dump_to_file=True, output_file='./outputLW_tapplus_sync/lws_Spatial_polygon.txt', output_format='ipac')
 
──────────
 
        koaid          ...   dec   
---------------------- ... --------
LW.20021113.44213.fits ... 17.86405
LW.20021113.44828.fits ... 17.86406
LW.20030220.22189.fits ...   17.525
LW.20030220.23158.fits ...   17.525
LW.20010312.19037.fits ...   17.528
LW.19990823.52297.fits ...   17.528
LW.19990823.52460.fits ...   17.528
LW.19990823.53149.fits ...   17.528
LW.19990823.53945.fits ...   17.528
LW.19990823.54734.fits ...   17.528
                   ... ...      ...
LW.19991028.50618.fits ... 17.52735
LW.19991028.50744.fits ... 17.52735
LW.19991123.44243.fits ...   17.862
LW.19991123.44614.fits ...   17.862
LW.19991122.40111.fits ...    17.53


## Count number of records on date

In [15]:
print("sql=(\"select count(*) from " + koatable + " where date_obs=to_date('" + date + "', 'YYYY-MM-DD')\")")
print("job = koa.launch_job(sql)")
print("r = job.get_results()")
print("print(r)")
print(" ")
print('─' * 10)
print(" ")


sql=("select count(*) from " + koatable + " where date_obs=to_date('" + date + "', 'YYYY-MM-DD')")
job = koa.launch_job(sql)
r = job.get_results()
print(r)

sql=("select count(*) from koa_lws where date_obs=to_date('1998-12-03', 'YYYY-MM-DD')")
job = koa.launch_job(sql)
r = job.get_results()
print(r)
 
──────────
 
count(*)
--------
      63


 ## Count total number of records in table

In [16]:
print("sql=\"select count(*) as total from " + koatable + "\"")
print("job = koa.launch_job(sql)")
print("r = job.get_results()")
print("print(r)")
print(" ")
print('─' * 10)
print(" ")

sql="select count(*) as total from " + koatable
job = koa.launch_job(sql)
r = job.get_results()
print(r)

sql="select count(*) as total from koa_lws"
job = koa.launch_job(sql)
r = job.get_results()
print(r)
 
──────────
 
total
-----
 2000


# Note: There are 23,737 records that satisfy this query, but TAP+ only returns the first 2,000 in synchronous mode

-----------------

<font color="#480000">Visit KOA at https://koa.ipac.caltech.edu.  

<font color="#480000"> The Keck Observatory Archive (KOA) is a collaboration between the NASA Exoplanet Science Institute (NExScI) and the W. M. Keck Observatory (WMKO). NExScI is sponsored by NASA's Exoplanet Exploration Program, and operated by the California Institute of Technology in coordination with the Jet Propulsion Laboratory (JPL).

    
<font color="#480000"> Need help? Submit your questions to the KOA Help Desk at https://koa.ipac.caltech.edu/cgi-bin/Helpdesk/nph-genTicketForm?projname=KOA